In [336]:
import torch
import torch.utils.data
from torch.optim import SGD, Adam
from torch.nn import Linear, Sigmoid, Dropout, Softmax, Sequential, ReLU
from torch.nn.functional import one_hot
import plotly.express as px
import plotly.graph_objects as go
import pandas as pd

# Задание 1

In [163]:
import numpy as np
def sample_data():
    count = 10000
    rand = np.random.RandomState(0)
    a = 0.3 + 0.1 * rand.randn(count)
    b = 0.8 + 0.05 * rand.randn(count)
    mask = rand.rand(count) < 0.5
    samples = np.clip(a * mask + b * (1 - mask), 0.0, 1.0)
    return np.digitize(samples, np.linspace(0.0, 1.0, 100))

In [164]:
def p(theta, x):
    return torch.exp(theta[x]) / torch.sum(torch.exp(theta))

def J(output):
    return -torch.sum(torch.log(output))

In [165]:
theta = torch.zeros(100, requires_grad=True)
sgd = SGD([theta], lr=0.03)

num_epochs = 20
losses = []
sample = sample_data()
size_train = int(len(sample) * 0.8)
size_test = len(sample) - size_train
train, test = torch.utils.data.random_split(sample, (size_train, size_test))

x_train = torch.tensor(train, dtype=torch.long)
x_test = torch.tensor(test, dtype=torch.long)
dataset = torch.utils.data.DataLoader(x_train, batch_size=1000, shuffle=True)
train_losses = []
test_losses = []
for i in range(num_epochs):
    for x1 in dataset:
        sgd.zero_grad()
        output = p(theta, x1)
        loss = J(output)
        losses.append(float(loss))
        loss.backward()
        sgd.step()
    train_losses.append(float(J(p(theta, x_train)).double()) / size_train)
    test_losses.append(float(J(p(theta, x_test)).double()) / size_test)

In [166]:
df = pd.DataFrame()
df['loss'] = train_losses + test_losses
df['data'] = ['train'] * num_epochs + ['test'] * num_epochs
df['iter'] = list(range(num_epochs)) + list(range(num_epochs))

In [167]:
px.line(df, x='iter', y='loss', color='data')

In [168]:
predicted = p(theta, range(100)).tolist()
expected = np.zeros(100)
for x in sample[:1000]:
    expected[x] += 1
expected /= 1000
expected = list(expected)

df = pd.DataFrame()
df['prob'] = expected + predicted
df['data'] = ['expected'] * 100 + ['predicted'] * 100
df['val'] = list(range(100)) + list(range(100))

In [169]:
px.line(df, x='val', y='prob', color='data')

# Задание 2

In [193]:
dist = np.load('distribution.npy')

In [299]:
def gen_pair():
    x1 = np.random.choice(200, p=np.sum(dist, axis=1))
    x2 = np.random.choice(200, p=dist[x1] / np.sum(dist[x1]))
    return (x1, x2)

In [300]:
sample = np.array([gen_pair() for i in range(100000)])

In [304]:
size_train = int(len(sample) * 0.8)
size_test = len(sample) - size_train
train, test = torch.utils.data.random_split(sample, (size_train, size_test))

In [305]:
x_train = torch.tensor(train)
x_test = torch.tensor(test)
dataset = torch.utils.data.DataLoader(x_train, batch_size=1000, shuffle=True)

In [306]:
def p(theta, x):
    return torch.exp(theta[x]) / torch.sum(torch.exp(theta))

def J(output):
    return -torch.sum(torch.log(output))

In [343]:
theta = torch.zeros(200, requires_grad=True)
mlp = Sequential(
            Linear(200, 15),
            ReLU(),
            Dropout(0.07),
            Linear(15, 15),
            Sigmoid(),
            Dropout(0.07),
            Linear(15, 15),
            Sigmoid(),
            Dropout(0.07),
            Linear(15, 200),
            ReLU(),
            Dropout(0.07),
            Softmax(dim=1)
        )

sgd = Adam([theta, *mlp.parameters()])
#sgd = SGD([theta, *mlp.parameters()], lr=0.03)
num_epochs = 20

In [344]:
train_losses = []
test_losses = []
for i in range(num_epochs):
    for batch in dataset:
        x1 = batch[:,0]
        x2 = batch[:,1]
        onehots = one_hot(x1, 200).float()
        sgd.zero_grad()
        px1 = p(theta, x1)#.reshape(len(batch))
        px2 = mlp(onehots)[range(len(batch)), x2]#.reshape(len(batch))
        output = px1 * px2
        
        loss = J(output)
        losses.append(float(loss))
        loss.backward()
        sgd.step()
    train_losses.append(float(J(p(theta, x_train)).double()) / size_train)
    test_losses.append(float(J(p(theta, x_test)).double()) / size_test)

In [345]:
df = pd.DataFrame()
df['loss'] = train_losses + test_losses
df['data'] = ['train'] * num_epochs + ['test'] * num_epochs
df['iter'] = list(range(num_epochs)) + list(range(num_epochs))

In [346]:
px.line(df, x='iter', y='loss', color='data')

In [311]:
x = sample[:,1]
y = sample[:,0]
fig = go.Figure(go.Histogram2d(x=x, y=y, histnorm='probability', nbinsx=200, nbinsy=200))
fig.show()

In [350]:
px1 = p(theta, range(200))
predicted = []
for i in range(200):
    print(px1[i])
    predicted.append((mlp(one_hot(torch.tensor([i]), 200).float())[0] * px1[i]).tolist())

tensor(0.0040, grad_fn=<SelectBackward>)
tensor(0.0041, grad_fn=<SelectBackward>)
tensor(0.0042, grad_fn=<SelectBackward>)
tensor(0.0044, grad_fn=<SelectBackward>)
tensor(0.0041, grad_fn=<SelectBackward>)
tensor(0.0039, grad_fn=<SelectBackward>)
tensor(0.0037, grad_fn=<SelectBackward>)
tensor(0.0040, grad_fn=<SelectBackward>)
tensor(0.0043, grad_fn=<SelectBackward>)
tensor(0.0040, grad_fn=<SelectBackward>)
tensor(0.0042, grad_fn=<SelectBackward>)
tensor(0.0039, grad_fn=<SelectBackward>)
tensor(0.0038, grad_fn=<SelectBackward>)
tensor(0.0041, grad_fn=<SelectBackward>)
tensor(0.0037, grad_fn=<SelectBackward>)
tensor(0.0037, grad_fn=<SelectBackward>)
tensor(0.0042, grad_fn=<SelectBackward>)
tensor(0.0041, grad_fn=<SelectBackward>)
tensor(0.0037, grad_fn=<SelectBackward>)
tensor(0.0039, grad_fn=<SelectBackward>)
tensor(0.0038, grad_fn=<SelectBackward>)
tensor(0.0037, grad_fn=<SelectBackward>)
tensor(0.0037, grad_fn=<SelectBackward>)
tensor(0.0036, grad_fn=<SelectBackward>)
tensor(0.0039, g

tensor(0.0041, grad_fn=<SelectBackward>)


In [348]:
fig = go.Figure(go.Heatmap(z=predicted))
fig.show()

In [295]:
fig = go.Figure(go.Heatmap(z=dist))
fig.show()